In [1]:
### Section with all imports ###
## Standard Python Library imports ##
from copy import deepcopy
from datetime import datetime
from datetime import timedelta
from typing import List
from typing import Tuple

import glob
import os
import re

## Anaconda imports ##
from matplotlib import cm
from mpl_toolkits.axes_grid1 import make_axes_locatable
from pandas import DataFrame
from pandas.plotting import register_matplotlib_converters
from tqdm import tqdm_notebook as tqdm

import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns

In [2]:
project = 'medicin_prices'
subfolders = ['raw_data','parsed_data']

raw_data = os.path.join(project, subfolders[0])
# Special folder that is write protected in order to preserve the original data
raw_data_read_only = os.path.join(project, subfolders[0] + '-read-only')
raw_data_read_only_limited = os.path.join(project, subfolders[0] + '-read-only-lmt')
parsed_data = os.path.join(project, subfolders[1])
work_on_dir = raw_data_read_only

In [3]:
# Get all csv files
def get_csv_files(data_path):
    return glob.glob(os.path.join(data_path, '*.csv'))

In [4]:
def find_single_contender_idx(df: DataFrame):
    return df.isnull().sum(axis=1) == df.shape[1] - 1

In [5]:
def clean_dataframe(df: DataFrame):
    # Remove these columns if they are present in the data frame
    unwanted_columns = ['Unnamed: 0', 'tilskudspris']
    for unwanted_column in unwanted_columns:
        if unwanted_column in df.columns:
            df.drop(unwanted_column, axis=1, inplace=True)
    # Convert datetime column into a datetime time and store it in date
    df['date'] = pd.to_datetime(df['datetime'], format='%d.%m.%Y')
    # Drop the datetime column
    df.drop('datetime', axis=1, inplace=True)
    # Set the date column to be the index
    df.set_index('date', inplace=True)
    # Find index set with only one contender
    tmp = df[find_single_contender_idx(df)]
    # There might have been multiple contender from product launch
    if not tmp.empty:
        # Grab the first index of these
        new_start_index = tmp.index.values[0]
        # Slice such that we skip only NaN rows from the start
        df = df[new_start_index:].copy()
    return df

In [6]:
def find_pct_above_idx(df: DataFrame, threshold=0.5):
    return ((df > threshold).sum(axis=1) > 0 & (find_single_contender_idx(df)))

In [7]:
def find_pct_change_above(df: DataFrame, threshold=0.5):
    return df.loc[((df > threshold).sum(axis=1) > 0) & (df.isnull().sum(axis=1) == df.shape[1] - 1), :]

In [8]:
csv_files_limited = get_csv_files(raw_data_read_only)

In [9]:
# A product number regex matcher
product_number_matcher = re.compile('[0-9]{6}')

def find_all_above(csv_files: List[str], pct_threshold=0.5, periods=2):
    """Run through a list of csv files and find entries above a percentage threshold given a number of periods

    Keyword arguments:
        csv_files     -- A list of paths point to csv files
        pct_threshold -- Percentage threshold that the price hike should be larger than (defaults to 50%, i.e. 0.5)
        periods -- Periods defines the periods between measurements to compute the percentage difference between.
                   e.g. periods=2, compute between, period 1: x_2 / x_1, period 2: x_3 / x_1
    """
    # Create a dictionary for storing the results
    product_numbers = dict()
    # Keep track of product numbers already processed
    already_processed = []
    # Run throught all the csv files we where given
    for i in tqdm(range(len(csv_files))):
        f = csv_files[i]
        # Find product number
        product_number = product_number_matcher.search(f).group()
        # Check whether the product number has already been processed
        if product_number in already_processed:
            continue
        # Read the csv file
        df = pd.read_csv(f)
        # Clean the data frame
        df = clean_dataframe(df)
        # Check if we have already processed the product number before
        already_processed.extend(df.columns.tolist())
        # Find percentage change over the number of periods
        pct_changed = df.pct_change(periods)
        # Find places where there are only one contender
        single_pct_frame = pct_changed[find_single_contender_idx(pct_changed)]
        # Find all periods where the percentage change is above the given threshold
        above_pct = find_pct_change_above(single_pct_frame, threshold=pct_threshold)
        above_idx = find_pct_above_idx(single_pct_frame, threshold=pct_threshold)
        # Store the result, if the frame is non empty
        if not above_pct.empty:
            product_numbers[product_number] = {'pct_change': above_pct, 'idx': above_idx}
    # Return result
    return product_numbers

In [10]:
possible_price_hikes = find_all_above(csv_files_limited, pct_threshold=7.5, periods=10)

In [11]:
def add_periods(date: datetime, periods: int) -> datetime:
    """Function for adding a number of periods to a datetime

    Keyword arguments:
        date    -- A datetime to add a number of 14 days periods to
        periods -- Number of periods to add to the datetime
    Returns:
        The date plus a number of periods (periods can be negative)
    """
    number_of_days_to_add = periods * 14
    return date + timedelta(days=number_of_days_to_add)

def extraction_period(date: datetime, periods: int=8) -> (datetime, datetime):
    """Function for creating a date +/- a number of periods

    Keyword arguments:
        date    -- A datetime to add a number of 14 days periods to
        periods -- Number of periods to add to the datetime
    Returns:
        A tuple of two dates, such that tuple = (datetime1, datetime2), where datetime1 = date - period,
        datetime2 = date + period
    """    
    return (add_periods(date, -periods), add_periods(date, periods))

In [12]:
def extract_above_indices(d_elem):
    """Function for extracting indices from a bool sets where it is True

    Keyword arguments:
        d_elem   -- A dictionary element containing a ['idx'] value containing a dataframe or series with bools
    Returns:
        Index set
    """
    return d_elem['idx'][d_elem['idx'] == True].index

In [13]:
def expand_date_indices(date_indices, periods=8):
    """Function for expanding a list of dates into a list of tuples of dates

    Keyword arguments:
        date_indices -- A datetime index
        periods      -- Number of periods to expand each date with
    Returns:
        A list of tuples l = [t_1, t_2, ..., t_n], such that t_i = (date_i - periods, date_i + periods)
    """
    expanded_date_list = []
    for date_elem in date_indices:
        expanded_date = extraction_period(date_elem, periods=periods)
        expanded_date_list.append(expanded_date)
    return expanded_date_list

In [14]:
def merge_periods(dates: List[Tuple[datetime, datetime]]) -> List[Tuple[datetime, datetime]]:
    """Function for merging time periods if they overlap, takes a list of tuples containing datetime elements.

    Keyword arguments:
        dates -- A list of tuples containing datetime elements. The function takes two consecutive tuples t1 and t2
                 and merges them into a single tuple if they overlap
    Returns:
        A list of tuples of non overlap date periods
    """
    def date_intersection(dt1: datetime, dt2: datetime) -> bool:
        """Helper function that determines if the second element of dt1 is containg within dt2
        
        Returns:
            True if there is overlap, False otherwise
        """
        return dt1[1] >= dt2[0] and dt1[1] < dt2[1]
    
    def merge_tuple(t1: Tuple[datetime, datetime], t2: Tuple[datetime, datetime]) -> Tuple[datetime, datetime]:
        """Helper function that merges two tuple into a single tuple

        Returns:
            A new tuple such that t_new = (dt1[0], dt2[1])
        """        
        return (t1[0], t2[1])
    
    def has_intersections(date_list):
        """Helper function that determines whether a list of date tuples still have intersections (overlap

        Returns:
            True if intersections exists, False otherwise
        """                
        intersects = []
        for i in range(len(date_list)-1):
            d1 = date_list[i]
            d2 = date_list[i+1]
            dates_intersects = date_intersection(d1, d2)
            intersects.append(dates_intersects)
        any_intersections = any(intersects)
        return any(intersects)

    # Make a copy of our dates, otherwise we change the original list
    compute_list = deepcopy(dates)
    # Sanity check, does our list of dates contain more than one tuple
    if len(compute_list) == 1:
        return compute_list
    # Loop while the sorted list of date tuples still has intersections
    while has_intersections(sorted(compute_list)):
        # Extract two dates tuples, date1 = (datetime1, datetime2)
        date1 = compute_list.pop(0)
        date2 = compute_list.pop(0)
        # does the dates tuples intersect / is there overlap in the time period?
        if date_intersection(date1, date2):
            # The two dates overlapped, merge them into a new date tuple
            new_date = merge_tuple(date1, date2)
            # Append the new date tuple to the list
            compute_list = [new_date] + compute_list
        else:
            # No overlap was found, simply append the dates to the end of the list (we pop from the start of the list)
            compute_list.append(date1)
            compute_list.append(date2)
        # We have merged everything except for one element, hence we need to break the while loop
        if len(compute_list) == 1:
            break
    # Return the merged result sorted
    return sorted(compute_list)

In [15]:
def load_product_dataframe(product_number) -> DataFrame:
    """Function for loading a dataframe given a product number

    Keyword arguments:
        product_number -- product number for which to load a dataframe

    Returns:
        A cleaned dataframe
    """
    df_path = os.path.join(work_on_dir, '{}.csv'.format(product_number))
    df = clean_dataframe(pd.read_csv(df_path))
    return df

In [16]:
# start by defining a Project name
project = 'medicin_prices'
 # generel package for interacting with the system
# among other things automate folder creation
def maybe_create_dir(path):
    if not os.path.isdir(path):
        os.mkdir(path)

maybe_create_dir(project)

subfolders = ['images']

for directory in subfolders: 
    maybe_create_dir(os.path.join(project, directory))

In [17]:
def generate_plot_and_save(df: DataFrame, start_date: datetime, end_date: datetime, save_path):
    # Set figure size
    fig = plt.figure(figsize=(15,15))
    # extract the period of time we want to plot, make a copy
    plot_data = df.loc[start_date:end_date].copy()
    # if we have more than one column, drop any column that are all NaN
    if len(plot_data.columns.tolist()) > 1:
        plot_data.dropna(axis=1, inplace=True, how='all')
    # Extract the name of the column that are 'single' at the point of price hike
    product_name = plot_data.columns[plot_data.notnull().any() == True][0]
    # Set title
    plt.title('Prisstigning for produkt nummer: {}'.format(product_name)) # , fontdict = {'fontsize' : 20}
    # Increase font size to make it look nice
    plt.rc('axes', titlesize=28, labelsize=24)
    # If we only have one product in the plot, skip having a legend
    legend_type = False if len(plot_data.columns.tolist()) == 1 else 'full'
    # Make a line plot of the data
    g = sns.lineplot(data=plot_data, legend=legend_type)
    # If there is a legend, increase font size
    if legend_type:
        plt.setp(g.get_legend().get_texts(), fontsize='18') # for legend text
        plt.setp(g.get_legend().get_title(), fontsize='20') # for legend title
    # Increase linewidth
    for l in g.lines:
        plt.setp(l,linewidth=3)
    # Set x- and y-labels
    plt.xlabel('Dato (åååå-mm)')
    plt.ylabel('Pris (kr)')
    # Increase font on x- and y-ticks, also rotate xticks 45 degrees
    plt.xticks(fontsize=20, rotation=45)
    plt.yticks(fontsize=20)
    # Get dates for plot name
    start_tag = start_date.date()
    end_tag = end_date.date()
    # Save the figure
    plt.savefig('{}_{}_{}.png'.format(os.path.join(save_path, product_name), start_tag, end_tag))
    # Close the figure after saving to disk to preserve memory
    plt.close(fig)

In [18]:
def generate_all_plots(dictionary, save_dir=os.path.join(project, 'images')):
    for pn, pct_idx in dictionary.items():
        print('Generating plot for: {}'.format(pn))
        idxs = extract_above_indices(pct_idx)
        expanded_dates = expand_date_indices(idxs, periods=16)
        merged_dates = merge_periods(expanded_dates)
        product_dataframe = load_product_dataframe(pn)
        for period in merged_dates:
            start_date, end_date = period
            generate_plot_and_save(product_dataframe, start_date, end_date, save_dir)

In [19]:
register_matplotlib_converters()

generate_all_plots(possible_price_hikes)

Generating plot for: 412129
Generating plot for: 062826
Generating plot for: 512521
Generating plot for: 570006
Generating plot for: 077640
Generating plot for: 012718
Generating plot for: 447449
Generating plot for: 032660
Generating plot for: 599280
Generating plot for: 145958
Generating plot for: 092171
Generating plot for: 414991
Generating plot for: 010234
Generating plot for: 104992
Generating plot for: 110333
Generating plot for: 407740
Generating plot for: 126093
Generating plot for: 397192
Generating plot for: 056732
Generating plot for: 133440
Generating plot for: 191986
Generating plot for: 066354
Generating plot for: 074733
Generating plot for: 466696
Generating plot for: 483749
Generating plot for: 012693
Generating plot for: 170298


In [20]:
def find_atleast_contender_idx(df: DataFrame, contenders=1):
    return df.isnull().sum(axis=1) <= df.shape[1] - contenders

In [21]:
def find_streaks(csv_files: List[str]):
    """Run through a list of csv files and find entries above a percentage threshold given a number of periods

    Keyword arguments:
        csv_files  -- A list of paths point to csv files
    """
    # Create a dictionary for storing the results
    product_numbers = dict()
    # Keep track of product numbers already processed
    already_processed = []
    # Run throught all the csv files we where given
    for i in tqdm(range(len(csv_files))):
        f = csv_files[i]
        # Find product number
        product_number = product_number_matcher.search(f).group()
        # Check whether the product number has already been processed
        if product_number in already_processed:
            continue
        # Read the csv file
        df = pd.read_csv(f)
        # Clean the data frame
        df = clean_dataframe(df)
        df_columns = df.columns.tolist()
        # Check if we have already processed the product number before
        already_processed.extend(df_columns)
        # We are only interested in dataframe that has atleast two columns
        if len(df_columns) < 2:
            continue
        # Extract indices where there are atleast two contenders
        df['min_idx'] = df.idxmin(axis=1)
         # At least two contenders, plus one for the min_idx column
        two_or_more_idx = find_atleast_contender_idx(df.drop(['min_idx'], axis=1), 2)
        df_two_or_more = df.loc[two_or_more_idx].copy()
        df_two_or_more['category-code'] = pd.Categorical(df_two_or_more['min_idx']).codes
        product_numbers[product_number] = df_two_or_more
        
    # Return result
    return product_numbers

In [22]:
files_with_streaks = find_streaks(csv_files_limited)

In [23]:
def save_min_product_price_plot(product_number, df, save_path=os.path.join(project, 'images')):  
    # Find number of different categories
    unique_cats = df['category-code'].unique()
    # Find number of 'bins'
    num_bins = df['category-code'].shape[0]
    # Find category minimum value
    min_value = unique_cats.min()
    # Find category maximum value
    max_value = unique_cats.max()
    # Define the colormap
    cmap = plt.cm.jet
    # Define the bins and normalize
    bounds = np.linspace(min_value, max_value, len(unique_cats))
    norm = mpl.colors.BoundaryNorm(bounds, cmap.N)
    df_plot = pd.DataFrame((np.array(df['category-code'])))
    fig = plt.figure(figsize=(14,1))
    ax = plt.subplot()
    # Transpose the category data to make a horizontal plot
    im = ax.imshow(df_plot.transpose(),
                   cmap=cmap,
                   interpolation=None,
                   vmin=min_value,
                   vmax=max_value,
                   aspect='auto',
                   norm=norm)
    # Remove ticks from top, bottom and left axis, and distable labels
    plt.tick_params(
        axis='both',       # changes apply to the x-axis
        which='both',      # both major and minor ticks are affected
        bottom=False,      # ticks along the bottom edge are off
        top=False,         # ticks along the top edge are off
        left=False,        # ticks along the left edge are off
        labelbottom=False) # labels along the bottom edge are off
    # Make axis locatable 
    divider = make_axes_locatable(ax)
    # Append an axis to the right
    cbax = divider.append_axes("right", size="5%", pad=0.10)
    # Add a colorbar to the right axis
    cb = plt.colorbar(im,
                      cax=cbax,
                      cmap=cmap,
                      boundaries=bounds,
                      spacing='proportional')
    # Set the colorbar label
    cb.set_label('Category')
    # Disable formmatter on both axis
    ax.xaxis.set_major_formatter(plt.NullFormatter())
    ax.yaxis.set_major_formatter(plt.NullFormatter())
    # Save the figure as streak  plot
    plt.savefig('{}_streakplot.png'.format(os.path.join(save_path, product_number)))
    # Close the figure after saving to disk to preserve memory
    plt.close(fig)

In [24]:
def generate_all_streak_plots(dictionary, save_dir=os.path.join(project, 'images')):
    for pn, df in dictionary.items():
        if len(df['category-code'].unique()) == 1:
            continue
        try:
            save_min_product_price_plot(pn, df)
        except (ZeroDivisionError, ValueError) as exc:
            # We caught an error, remove the file
            if os.path.exists(os.path.join(project, 'images', '{}_steakplot.png'.format(pn))):
                os.remove(filePath)

In [25]:
generate_all_streak_plots(files_with_streaks)

/home/mian/bin/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:16: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  app.launch_new_instance()


Error in callback <function install_repl_displayhook.<locals>.post_execute at 0x7f32aaea2378> (for post_execute):


ZeroDivisionError: division by zero

ZeroDivisionError: division by zero

<Figure size 1008x72 with 2 Axes>

...

<Figure size 1008x72 with 2 Axes>

ZeroDivisionError: division by zero

<Figure size 1008x72 with 2 Axes>

ZeroDivisionError: division by zero

<Figure size 1008x72 with 2 Axes>